<a href="https://colab.research.google.com/github/kimo722504/practice_ML/blob/master/tx2__reid.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# TX2 에서 reid 돌리기
이 [깃허브](https://github.com/giranntu/Human-ReID-in-NVIDIA-Jetson)를 그대로 따라했습니다.

In [0]:
!pip3 install tensorflow==1.11.0

     |████████████████████████████████| 63.0MB 2.1MB/s 
     |████████████████████████████████| 3.0MB 37.2MB/s 
     |████████████████████████████████| 573kB 45.4MB/s 
ERROR: magenta 0.3.19 has requirement tensorflow>=1.12.0, but you'll have tensorflow 1.11.0 which is incompatible.
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.8.3 which is incompatible.
  Found existing installation: tensorboard 1.14.0
    Uninstalling tensorboard-1.14.0:
      Successfully uninstalled tensorboard-1.14.0
  Found existing installation: setuptools 41.0.1
    Uninstalling setuptools-41.0.1:
      Successfully uninstalled setuptools-41.0.1
  Found existing installation: tensorflow 1.14.0
    Uninstalling tensorflow-1.14.0:
      Successfully uninstalled tensorflow-1.14.0


In [0]:
import numpy,tensorflow as tf,cv2,pprint # 설치 되있는지 
print(tf.__version__)
print(cv2.__version__)
print(numpy.__version__)

1.14.0
3.4.3
1.16.4


## DukeMTMC-reID 데이터
구글에서 다운로드 한다음에 colab에 업로드 후 압축을 풉니다.

저는 [구글드라이브](https://drive.google.com/open?id=1jjE85dRCMOgRtvJ5RQV9-Afs-2_5dY3O)  에서 받았습니다  
구글 -> [중국사이트](https://blog.csdn.net/Layumi1993/article/details/72716551) -> 구글드라이브  
~~찝찝하지만.. 학습은 잘됩니다~~

In [0]:
%cd /content
!unzip /content/DukeMTMC-reID.zip

/content
Archive:  /content/DukeMTMC-reID.zip
   creating: DukeMTMC-reID/
  inflating: DukeMTMC-reID/.DS_Store  
   creating: DukeMTMC-reID/bounding_box_test/
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044158.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044278.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044398.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044518.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044638.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044758.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044878.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0044998.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0045118.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0045238.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0045358.jpg  
  inflating: DukeMTMC-reID/bounding_box_test/0002_c1_f0045478.jpg  
  inflating: DukeMTMC-reI

## REAME 따라하기
이밑으로는  
위에 소개된 [깃허브](https://github.com/giranntu/Human-ReID-in-NVIDIA-Jetson)에 소개되어있는대로 그대로 따라했습니다.

In [0]:
!git clone https://github.com/giranntu/Human-ReID-in-NVIDIA-Jetson.git

Cloning into 'Human-ReID-in-NVIDIA-Jetson'...
remote: Enumerating objects: 54, done.
remote: Total 54 (delta 0), reused 0 (delta 0), pack-reused 54
Unpacking objects: 100% (54/54), done.


In [0]:
%cd Human-ReID-in-NVIDIA-Jetson/

/content/Human-ReID-in-NVIDIA-Jetson


In [0]:
!cat setup.sh

mkdir models
mkdir models/id
mkdir models/reid
CHECKPOINT_DIR=pretrained
mkdir ${CHECKPOINT_DIR}
wget http://download.tensorflow.org/models/resnet_v1_50_2016_08_28.tar.gz
tar -xvf resnet_v1_50_2016_08_28.tar.gz
mv resnet_v1_50.ckpt ${CHECKPOINT_DIR}
rm resnet_v1_50_2016_08_28.tar.gz


In [0]:
!bash setup.sh

mkdir: cannot create directory ‘pretrained’: File exists
--2019-08-20 00:53:56--  http://download.tensorflow.org/models/resnet_v1_50_2016_08_28.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 74.125.141.128, 2607:f8b0:400c:c06::80
Connecting to download.tensorflow.org (download.tensorflow.org)|74.125.141.128|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 95073259 (91M) [application/x-tar]
Saving to: ‘resnet_v1_50_2016_08_28.tar.gz’

resnet_v1_50_2016_0 100%[===================>]  90.67M  99.1MB/s    in 0.9s    

2019-08-20 00:53:57 (99.1 MB/s) - ‘resnet_v1_50_2016_08_28.tar.gz’ saved [95073259/95073259]

resnet_v1_50.ckpt


In [0]:
%cd /content/DukeMTMC-reID/

/content/DukeMTMC-reID


In [0]:
!mv query bounding_box_query

In [0]:
%cd /content/Human-ReID-in-NVIDIA-Jetson/

/content/Human-ReID-in-NVIDIA-Jetson


## utils/dataset.py
다른 데이터 쓰려면 get_class_from_path 수정하면 된다고 나와있습니다.   
저는 커스텀 데이터를 사용하지 않기때문에 따로 수정하지 않았습니다.

In [0]:
!cat /content/Human-ReID-in-NVIDIA-Jetson/utils/dataset.py 

from glob import glob
import numpy as np
import random

class ImageDataset(object):
    def __init__(self, data_dir, **kwargs):
        self.data_dir = data_dir
        self.h = kwargs.get('h', 256)
        self.w = kwargs.get('w', 128)
        self.all_img_files = self.get_all_jpgs()
        self.id_dict, self.count = self.get_classes_dict()

    def get_class_from_path(self, path):
        #IF USING DIFFERENT DATASET: change this to be correct.
        #this assumes that all images are in some directory, d
        #and their paths are d/<<ID>>_<OTHER_INFO>.jpg, as in Duke or Market.
        return int(path.split('/')[-1].split('_')[0])

    def get_classes_dict(self):
        id_list = []
        count = 0
        for img_file in self.all_img_files:
            person_id = self.get_class_from_path(img_file)
            if person_id not in id_list:
                id_list += [person_id]
                count += 1
        id_list.sort()
        id_dict = {}
        for i in range(len(i

In [0]:
!mv /content/DukeMTMC-reID/ /content/Human-ReID-in-NVIDIA-Jetson/data

## Training은 Auzre에서..
**train_id.sh**을 실행시키면 학습이 시작됩니다  
만  
**colab**사양에서는 12시간내에 학습이 이루어지지 않습니다.( colab은 12시간 이내만 무료)  

In [0]:
%cd /content/Human-ReID-in-NVIDIA-Jetson/
!bash train_id.sh

/content/Human-ReID-in-NVIDIA-Jetson
2019-08-20 00:54:26.892595: I tensorflow/core/platform/cpu_feature_guard.cc:141] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
False
excluding block block1
Initializing new variables..
[<tf.Variable 'resnet_v1_50/conv1/weights:0' shape=(7, 7, 3, 64) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_1/bottleneck_v1/shortcut/weights:0' shape=(1, 1, 64, 256) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_1/bottleneck_v1/conv1/weights:0' shape=(1, 1, 64, 64) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_1/bottleneck_v1/conv2/weights:0' shape=(3, 3, 64, 64) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_1/bottleneck_v1/conv3/weights:0' shape=(1, 1, 64, 256) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_2/bottleneck_v1/conv1/weights:0' shape=(1, 1, 256, 64) dtype=float32_ref>,
 <tf.Variable 'resnet_v1_50/block1/unit_2/bottleneck_v1/conv2/weights:

## Tensorboard
README대로 텐서보드에서  val loss가 평평해지는곳을 찾고 **train_reid.sh** 파일을 고쳐줍니다.
(저의경우 models/m0/model.ckpt-1501)

**train_reid.sh** 까지
실행후 나온 모델을 **scp명령어**를 통해 **jetson TX2**로 이동시킵니다.  
그 후 나머지 커맨대는 TX2에서 실행


## 마무리
본 실험의 학습부분은 azure에서 했습니다
학습 데이터의 결과는 구글 드라이브 **호영/reid-jetson** 에서 확인하시면 됩니다.  

이 폴더에 있는내용을 jetson으로 옮기면됩니다.